In [ ]:
# k-means clustering (generate data)
import numpy as np
import random
import matplotlib.pyplot as plt
from IPython.display import clear_output
from time import sleep

# generate data in two clusters
N     = 25 # number of data points
x_pos = np.random.rand(N,2)
x_neg = -x_pos
X     = np.vstack((x_pos, x_neg))
N     = 2*N

# display everything
plt.plot( X[:,0], X[:,1], 'o' )
plt.axis([-2, 2, -2, 2])
plt.show()

In [ ]:
# k-means clustering (cluster)
Niter = 25

c1 = X[random.randint(0,N-1),:] # initial cluster-1 center
c2 = X[random.randint(0,N-1),:] # initial cluster-2 center
for i in range(Niter):
    
    # determine class assignment
    m = np.zeros(N)
    for j in range(N):
        if( np.linalg.norm(X[j,:]-c1) < np.linalg.norm(X[j,:]-c2) ):
            m[j] = 1
        else:
            m[j] = 2
        
    # estimate class centers
    ind1 = np.where(m==1)
    ind2 = np.where(m==2)
    c1   = np.mean(X[ind1,:],axis=1)[0]
    c2   = np.mean(X[ind2,:],axis=1)[0]

    # display
    plt.scatter( X[:,0], X[:,1],  c=m, cmap=plt.cm.Paired) # plot data
    plt.plot( c1[0], c1[1], 'bo' ) # cluster-1 center
    plt.plot( c2[0], c2[1], 'ro' ) # cluster-2 center
    plt.show()
    sleep(0.1)
    clear_output(wait=True)

In [ ]:
# EM (generate data)

%reset -f

import numpy as np
import matplotlib.pyplot as plt
from IPython.display import clear_output
from time import sleep

numData  = 50 # number of data points per model
numIter  = 25 # maximum number of EM iterations
noise    = 0.2 # noise in data
sigma    = 0.075*0.075 # for E-step

# generate data (lines)
M1 = 2*np.random.rand(2)-1 # model-1 parameters
M2 = 2*np.random.rand(2)-1 # model-2 parameters

x1 = 2*np.random.rand(numData)-1
y1 = M1[0]*x1 + M1[1] + noise*(np.random.rand(numData)-0.5)
x2 = 2*np.random.rand(numData)-1
y2 = M2[0]*x2 + M2[1] + noise*(np.random.rand(numData)-0.5)

X = np.hstack((x1,x2)) # combine all data 
Y = np.hstack((y1,y2)) #

plt.plot(x1,y1,'ro')
plt.plot(x2,y2,'bo')
plt.plot((-1,1), (-M1[0]+M1[1], M1[0]+M1[1]),'r-')
plt.plot((-1,1), (-M2[0]+M2[1], M2[0]+M2[1]),'b-')


In [ ]:
# EM

# initialize model parameters
m1 = 2*np.random.rand(2)-1 
m2 = 2*np.random.rand(2)-1 

# EM iterations
sig = sigma
for i in range(numIter):
    # E-step
    r1  = m1[0]*X + m1[1] - Y # residual for model-1
    r2  = m2[0]*X + m2[1] - Y # residual for model-2

    den = np.exp(-(r1*r1)/sig) + np.exp(-(r2*r2)/sig)
    w1  = np.exp(-(r1*r1)/sig) / den # probability for model-1
    w2  = np.exp(-(r2*r2)/sig) / den # probability for model-2

    # plot intermediate model
    c1 = np.vstack((w1[0:numData],
                    np.zeros(numData),
                    1-w1[0:numData])).T # colormap
    c2 = np.vstack((w1[numData:2*numData],
                    np.zeros(numData),
                    1-w1[numData:2*numData])).T # colormap
    plt.scatter(x1,y1, s=30, c=c1, cmap=plt.cm.Paired) # plot data
    plt.scatter(x2,y2, s=30, c=c2, cmap=plt.cm.Paired) #
    plt.plot((-1,1), (-m1[0]+m1[1], m1[0]+m1[1]),'r-') # plot model
    plt.plot((-1,1), (-m2[0]+m2[1], m2[0]+m2[1]),'b-') #
    plt.show()
    sleep(1)
    clear_output(wait=True)
    
    # M-step
    M  = np.vstack((X,np.ones(2*numData))).T
    b  = np.vstack(Y)
    W1 = np.diag(w1*w1)
    W2 = np.diag(w2*w2)
    m1 = np.linalg.inv(M.T@W1@M)@M.T@W1@b
    m2 = np.linalg.inv(M.T@W2@M)@M.T@W2@b
    
    # update sigma
    sig0 = np.sum(w1*(r1*r1) + w2*(r2*r2)) / np.sum(w1 + w2)